In [0]:
configs = {"fs.azure.account.auth.type": "OAuth",
          "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
          "fs.azure.account.oauth2.client.id": "33e557d4-d040-46fa-b9e2-6847bfe22386",
          "fs.azure.account.oauth2.client.secret": dbutils.secrets.get(scope="adf1",key="FlightADLSKEY"),
          "fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/b71022e1-db54-4ee1-a8bb-eb361d24e2ea/oauth2/token"}
#dbutils.fs.mount(
  #source = "abfss://flightdata@indiaflightdata.dfs.core.windows.net/",
  #mount_point = "/mnt/flightdata",
  #extra_configs = configs)

#dbutils.fs.mount(
  #source = "abfss://bronzezoneconversions@indiaflightdata.dfs.core.windows.net/",
  #mount_point = "/mnt/bronzezoneconversions",
  #extra_configs = configs)

#dbutils.fs.mount(
  #source = "abfss://goldzoneflightstats@indiaflightdata.dfs.core.windows.net/",
  #mount_point = "/mnt/goldzoneflightstats",
  #extra_configs = configs)

#dbutils.fs.mount(
  #source = "abfss://silverzoneflightdata@indiaflightdata.dfs.core.windows.net/",
  #mount_point = "/mnt/silverzoneflightdata",
  #extra_configs = configs)


In [0]:
from pyspark.sql import functions as F
from pyspark.sql import SparkSession
from pyspark.sql.types import IntegerType, StringType

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Null Handling") \
    .getOrCreate()

# Define the file path
file_path = "/mnt/flightdata/Flight_Schedule.csv"

# Read the CSV file into a DataFrame
df = spark.read.csv(file_path, header=True, inferSchema=True)

# Define a dictionary to store data types for each column
column_data_types = {
    "airline": "STRING",
    "flightNumber": "INT",
    "origin": "STRING",
    "destination": "STRING",
    "daysOfWeek": "STRING",
    "scheduledDepartureTime": "TIMESTAMP",
    "scheduledArrivalTime": "TIMESTAMP",
    "timezone": "STRING",
    "validFrom": " DateType",
    "validTo": " DateType",
    "lastUpdated": " DateType"
}

# Iterate through each column and apply null handling based on its data type
for col, data_type in column_data_types.items():
    if data_type == "INT":
        df = df.withColumn(col, F.when(F.col(col).isNotNull(), F.col(col)).otherwise(-1).cast(IntegerType()))
    elif data_type == "TIMESTAMP":
         df = df.withColumn(col, F.when(F.col(col).isNotNull(), F.to_timestamp(F.concat(F.lit("1970-01-01 "), F.col(col)), "yyyy-MM-dd HH:mm")).otherwise(None))
    elif data_type == "STRING":
        df = df.withColumn(col, F.when(F.col(col).isNotNull(), F.col(col)).otherwise("NA").cast(StringType()))

# Write the DataFrame as a Parquet file
parquet_output_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"
df.write.parquet(parquet_output_path, mode="overwrite")

# Show the resulting DataFrame
df.display()


airline flightNumber origin destination daysOfWeek scheduledDepartureTime scheduledArrivalTime timezone validFrom validTo lastUpdated GoAir 425 Delhi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T05:45:00Z null 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 423 Delhi Hyderabad Saturday 1970-01-01T07:30:00Z null 2018-10-28 2018-10-28 2018-10-28 2023-11-05 GoAir 423 Delhi Hyderabad Friday 1970-01-01T07:30:00Z null 2018-12-01 2018-11-03 2018-12-01 2023-11-05 GoAir 423 Delhi Hyderabad Friday 1970-01-01T07:30:00Z null 2019-03-30 2019-02-02 2019-03-30 2023-11-05 GoAir 423 Delhi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Saturday 1970-01-01T07:30:00Z null 2018-11-30 2018-10-29 2018-11-30 2023-11-05 GoAir 423 Delhi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Saturday 1970-01-01T07:30:00Z null 2019-03-29 2019-02-01 2019-03-29 2023-11-05 GoAir 423 Delhi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T07:30:00Z null 2019-01-31 2018-12-02 2019-01-31 2023-11-05 GoAir 422 Delhi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T20:55:00Z null 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 559 Lucknow Hyderabad Sunday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T15:45:00Z 1970-01-01T17:45:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 580 Kochi Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T04:45:00Z 1970-01-01T06:15:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 587 Kochi Hyderabad Sunday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T17:20:00Z 1970-01-01T19:20:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 587 Kochi Hyderabad Monday 1970-01-01T17:50:00Z 1970-01-01T19:20:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 553 Ahmedabad Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday 1970-01-01T11:05:00Z 1970-01-01T12:45:00Z 2019-03-30 2018-10-29 2019-03-30 2023-11-05 GoAir 552 Ahmedabad Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T20:35:00Z 1970-01-01T22:20:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 553 Ahmedabad Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday 1970-01-01T11:00:00Z 1970-01-01T12:45:00Z 2019-10-26 2019-04-01 2019-10-26 2023-11-05 GoAir 552 Ahmedabad Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T20:40:00Z 1970-01-01T22:20:00Z 2019-10-26 2019-03-31 2019-10-26 2023-11-05 GoAir 701 Jaipur Hyderabad Saturday 1970-01-01T08:55:00Z 1970-01-01T10:55:00Z 2019-03-24 2018-10-28 2019-03-24 2023-11-05 GoAir 431 Jaipur Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T12:45:00Z 1970-01-01T15:05:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 385 Jaipur Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T17:55:00Z null 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 894 Bengaluru Hyderabad Saturday 1970-01-01T11:30:00Z 1970-01-01T12:40:00Z 2019-03-24 2018-10-28 2019-03-24 2023-11-05 GoAir 294 Bengaluru Hyderabad Saturday 1970-01-01T18:55:00Z null 2019-03-24 2018-10-28 2019-03-24 2023-11-05 GoAir 294 Bengaluru Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday 1970-01-01T18:55:00Z null 2019-03-30 2018-10-29 2019-03-30 2023-11-05 GoAir 894 Bengaluru Hyderabad Saturday 1970-01-01T11:40:00Z null 2019-10-20 2019-03-31 2019-10-20 2023-11-05 GoAir 952 Guwahati Hyderabad Sunday,Monday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01T07:25:00Z 1970-01-01T09:45:00Z 2019-03-30 2018-10-28 2019-03-30 2023-11-05 GoAir 373 Goa Hyderabad Saturday 1970-01-01T04:45:00Z null 2019-03-24 2018-10-28 2019-03-24 2023-11-05 GoAir 662 Goa Hyderabad Saturday 1970-01-01T10:45:00Z 1970-01-01T12:10:00Z 2019-03-24 2018-10-28 2019-03-24 2023-11-05 GoAir 370 Goa Hyderabad Monday 1970-01-01T19:45:00Z null 2019-03-26 2018-10-30 2019-03-26 2023-11-05 GoAir 370 Goa Hyderabad Sunday,Tuesday,Wednesday,Thursday,Friday,Saturday 1970-01-01

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, sum as spark_sum

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Null Handling") \
    .getOrCreate()

# Define the file path
file_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"

# Read the Parquet file into a DataFrame
df = spark.read.parquet(file_path)

# Calculate the count of null values in each column
null_counts = df.select([spark_sum(col(column).isNull().cast('int')).alias(column) for column in df.columns])

# Show the count of null values
print("Count of null values in each column:")
null_counts.display()

Count of null values in each column:


airline flightNumber origin destination daysOfWeek scheduledDepartureTime scheduledArrivalTime timezone validFrom validTo lastUpdated 0 415 0 0 0 30686 30968 0 0 0 0

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, count, round

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Airlines Data Analysis") \
    .getOrCreate()

# Read the Parquet file into a DataFrame
parquet_file_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"
df = spark.read.parquet(parquet_file_path)

# Group the data by airline to set it as the primary key
airline_grouped = df.groupBy("airline")

# Count the number of flights operated by each airline
airline_counts = airline_grouped.agg(count("*").alias("total_flights"))

# Calculate the total number of days
total_days = df.select("daysOfWeek").distinct().count()

# Calculate the average number of flights per day for each airline
avg_flights_per_day = airline_grouped.agg((count("*") / total_days).alias("avg_flights_per_day"))

# Calculate the total number of flights
total_flights = df.count()

# Calculate the market share for each airline as a percentage
airline_market_share = airline_grouped.agg((count("*") / total_flights * 100).alias("market_share"))

# Identify the top airlines with the highest number of flights
top_airlines = airline_counts.orderBy(col("total_flights").desc())

# Rename the columns to avoid duplicate columns after join
airline_counts = airline_counts.withColumnRenamed("total_flights", "total_flights_count")
avg_flights_per_day = avg_flights_per_day.withColumnRenamed("avg_flights_per_day", "avg_flights_per_day_count")
airline_market_share = airline_market_share.withColumnRenamed("market_share", "market_share_percentage")
top_airlines = top_airlines.withColumnRenamed("total_flights", "top_airlines_total_flights")

# Combine all tables into one by joining on the airline key
combined_table = airline_counts.join(avg_flights_per_day, "airline") \
    .join(airline_market_share, "airline") \
    .join(top_airlines, "airline")

# Save the combined table in Delta format to the specified location
output_path = "/mnt/silverzoneflightdata"
combined_table.write.format("delta").mode("overwrite").save(output_path + "/Flight Data")

# Show the combined table
combined_table.display()

combined_table.printSchema()


airline total_flights_count avg_flights_per_day_count market_share_percentage top_airlines_total_flights Akasa Air 438 3.4488188976377954 0.49223438448225487 438 FlyBig 214 1.68503937007874 0.24049807826301947 214 Air India 8185 64.44881889763779 9.198489582162685 8185 GoAir 11666 91.85826771653544 13.110516733721427 11666 SpiceJet 10824 85.22834645669292 12.164257939808051 10824 NA 675 5.31496062992126 0.7585803870445708 675 Jet Airways 1307 10.291338582677165 1.4688363938774134 1307 Star Air 472 3.716535433070866 0.5304443595333888 472 AirAsia India 5227 41.15748031496063 5.874221752714033 5227 IndiGo 41291 325.12598425196853 46.40376705401093 41291 Vistara 4332 34.110236220472444 4.8684003506327125 4332 IndiaOne Air 24 0.1889763779527559 0.026971747094918074 24 Alliance Air (India) 3069 24.165354330708663 3.449012159762649 3069 Jetlite 117 0.9212598425196851 0.1314872670877256 117 TruJet 1141 8.984251968503937 1.2822818098042301 1141

root
 |-- airline: string (nullable = true)
 |-- total_flights_count: long (nullable = false)
 |-- avg_flights_per_day_count: double (nullable = true)
 |-- market_share_percentage: double (nullable = true)
 |-- top_airlines_total_flights: long (nullable = false)



In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, count, explode, split

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Cities Data Analysis") \
    .getOrCreate()

# Read the Parquet file into a DataFrame
parquet_file_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"
df = spark.read.parquet(parquet_file_path)

# Split the "origin" and "destination" columns and explode them to create a row for each city
df = df.withColumn("origin_city", explode(split(col("origin"), ","))) \
    .withColumn("destination_city", explode(split(col("destination"), ",")))

# Group the data by city (origin and destination) and count the number of inbound and outbound flights for each city
city_flights = df.groupBy("origin_city").agg(
    count("*").alias("inbound_flights"),
    count("*").alias("outbound_flights")
).withColumnRenamed("origin_city", "city")

# Calculate the total number of flights for each city
city_flights = city_flights.withColumn("total_flights", city_flights["inbound_flights"] + city_flights["outbound_flights"])

# Identify the top cities with the highest number of flights
top_cities = city_flights.orderBy(col("total_flights").desc())

# Define the output path
output_path = "/mnt/silverzoneflightdata"

# Save the DataFrame as a Delta table with overwrite option set to true
city_flights.write.format("delta").mode("overwrite").save(output_path + "/city_flights")

# Show the results
print("City flights (inbound, outbound, total):")
city_flights.display()

print("Top cities with the highest number of flights (sorted by descending order):")
top_cities.display()

city_flights.printSchema()

City flights (inbound, outbound, total):


city inbound_flights outbound_flights total_flights Udaipur 327 327 654 Dimapur 102 102 204 Kochi 1258 1258 2516 Aurangabad 138 138 276 Bhubaneswar 1085 1085 2170 Aizwal 183 183 366 Mysore 154 154 308 MIHAN 967 967 1934 Jammu 823 823 1646 Jalgaon 43 43 86 Agartala 358 358 716 Bhuj 34 34 68 Darbhanga 85 85 170 Hubli 284 284 568 Patna 1187 1187 2374 Shirdi Airport 214 214 428 Jodhpur 284 284 568 Tezpur 26 26 52 Vadodara 303 303 606 Jaisalmer 66 66 132 Tiruchirappalli 162 162 324 Jharsuguda 103 103 206 Bhavnagar 33 33 66 Lucknow 1507 1507 3014 Chennai 4824 4824 9648 NA 500 500 1000 Shimla 42 42 84 Tezu 17 17 34 Dibrugarh 202 202 404 Kangra 83 83 166 Kandla 46 46 92 Thoise 6 6 12 Varanasi 892 892 1784 Calicut 222 222 444 Ranchi 848 848 1696 Kalaburgi (Gulbarga) 64 64 128 Mangalore 878 878 1756 Kolhapur 102 102 204 Mumbai 8301 8301 16602 Vidyanagar 31 31 62 Passighat 31 31 62 Goa 2251 2251 4502 Ahmedabad 3560 3560 7120 Bidar 14 14 28 Kolkata 6120 6120 12240 Belgaum 376 376 752 Jabalpur 184 184 368 Jorhat 40 40 80 Allahabad 261 261 522 Nasik 179 179 358 Ludhiana 19 19 38 Agatti 28 28 56 Gorakhpur 185 185 370 Porbandar 13 13 26 Amritsar 545 545 1090 Pantnagar 34 34 68 Gwalior 92 92 184 Lilabari 35 35 70 Keshod 9 9 18 Diu 22 22 44 Port Blair 1090 1090 2180 Shillong 86 86 172 Salem 10 10 20 Dehradun 504 504 1008 Surat 454 454 908 Silchar 172 172 344 Agra 63 63 126 Imphal 325 325 650 Pathankot 11 11 22 Adampur 13 13 26 Pakyong 15 15 30 Kadapa 70 70 140 Madurai 307 307 614 Bagdogra 663 663 1326 Khajuraho 24 24 48 Pune 2726 2726 5452 Nanded 70 70 140 Kannur International Airport 227 227 454 Delhi 13332 13332 26664 Durgapur 48 48 96 Pithoragarh 9 9 18 Raipur 616 616 1232 Chandigarh 1421 1421 2842 Rupsi 13 13 26 Pondicherry 18 18 36 Bilaspur 19 19 38 Nagpur 967 967 1934 Coimbatore 645 645 1290 Bhopal 375 375 750 Jamnagar 42 42 84 Tirupati 351 351 702 Thiruvananthapuram 522 522 1044 Tuticorin 78 78 156 Bengaluru 8941 8941 17882 Gaya 60 60 120 Kanpur 74 74 148 Bikaner 19 19 38 Hyderabad 5678 5678 11356 Bathinda 11 11 22 Rajkot 155 155 310 Vijayawada 397 397 794 Indore 1022 1022 2044 Srinagar 1897 1897 3794 Leh 327 327 654 Kishangarh 88 88 176 Guwahati 1430 1430 2860 Kullu 44 44 88 Rajahmundry 204 204 408 Jaipur 1615 1615 3230 Visakhapatnam 940 940 1880 Hindon Airport 9 9 18 Mundra 2 2 4 Cooch-Behar 1 1 2

Top cities with the highest number of flights (sorted by descending order):


city inbound_flights outbound_flights total_flights Delhi 13332 13332 26664 Bengaluru 8941 8941 17882 Mumbai 8301 8301 16602 Kolkata 6120 6120 12240 Hyderabad 5678 5678 11356 Chennai 4824 4824 9648 Ahmedabad 3560 3560 7120 Pune 2726 2726 5452 Goa 2251 2251 4502 Srinagar 1897 1897 3794 Jaipur 1615 1615 3230 Lucknow 1507 1507 3014 Guwahati 1430 1430 2860 Chandigarh 1421 1421 2842 Kochi 1258 1258 2516 Patna 1187 1187 2374 Port Blair 1090 1090 2180 Bhubaneswar 1085 1085 2170 Indore 1022 1022 2044 Nagpur 967 967 1934 MIHAN 967 967 1934 Visakhapatnam 940 940 1880 Varanasi 892 892 1784 Mangalore 878 878 1756 Ranchi 848 848 1696 Jammu 823 823 1646 Bagdogra 663 663 1326 Coimbatore 645 645 1290 Raipur 616 616 1232 Amritsar 545 545 1090 Thiruvananthapuram 522 522 1044 Dehradun 504 504 1008 NA 500 500 1000 Surat 454 454 908 Vijayawada 397 397 794 Belgaum 376 376 752 Bhopal 375 375 750 Agartala 358 358 716 Tirupati 351 351 702 Leh 327 327 654 Udaipur 327 327 654 Imphal 325 325 650 Madurai 307 307 614 Vadodara 303 303 606 Hubli 284 284 568 Jodhpur 284 284 568 Allahabad 261 261 522 Kannur International Airport 227 227 454 Calicut 222 222 444 Shirdi Airport 214 214 428 Rajahmundry 204 204 408 Dibrugarh 202 202 404 Gorakhpur 185 185 370 Jabalpur 184 184 368 Aizwal 183 183 366 Nasik 179 179 358 Silchar 172 172 344 Tiruchirappalli 162 162 324 Rajkot 155 155 310 Mysore 154 154 308 Aurangabad 138 138 276 Jharsuguda 103 103 206 Dimapur 102 102 204 Kolhapur 102 102 204 Gwalior 92 92 184 Kishangarh 88 88 176 Shillong 86 86 172 Darbhanga 85 85 170 Kangra 83 83 166 Tuticorin 78 78 156 Kanpur 74 74 148 Kadapa 70 70 140 Nanded 70 70 140 Jaisalmer 66 66 132 Kalaburgi (Gulbarga) 64 64 128 Agra 63 63 126 Gaya 60 60 120 Durgapur 48 48 96 Kandla 46 46 92 Kullu 44 44 88 Jalgaon 43 43 86 Shimla 42 42 84 Jamnagar 42 42 84 Jorhat 40 40 80 Lilabari 35 35 70 Pantnagar 34 34 68 Bhuj 34 34 68 Bhavnagar 33 33 66 Vidyanagar 31 31 62 Passighat 31 31 62 Agatti 28 28 56 Tezpur 26 26 52 Khajuraho 24 24 48 Diu 22 22 44 Bilaspur 19 19 38 Bikaner 19 19 38 Ludhiana 19 19 38 Pondicherry 18 18 36 Tezu 17 17 34 Pakyong 15 15 30 Bidar 14 14 28 Adampur 13 13 26 Porbandar 13 13 26 Rupsi 13 13 26 Bathinda 11 11 22 Pathankot 11 11 22 Salem 10 10 20 Pithoragarh 9 9 18 Hindon Airport 9 9 18 Keshod 9 9 18 Thoise 6 6 12 Mundra 2 2 4 Cooch-Behar 1 1 2

root
 |-- city: string (nullable = false)
 |-- inbound_flights: long (nullable = false)
 |-- outbound_flights: long (nullable = false)
 |-- total_flights: long (nullable = false)



In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, count, explode, split, max, struct

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Major Airlines in Cities") \
    .getOrCreate()

# Read the Parquet file into a DataFrame
parquet_file_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"
df = spark.read.parquet(parquet_file_path)

# Split the "origin" and "destination" columns and explode them to create a row for each city
df = df.withColumn("origin_city", explode(split(col("origin"), ","))) \
    .withColumn("destination_city", explode(split(col("destination"), ",")))

# Group the data by airline, origin city, and destination city to count the number of flights operated by each airline in each city
airline_city_counts = df.groupBy("airline", "origin_city", "destination_city").agg(count("*").alias("flights_count"))

# Find the major player (airline with the highest number of flights) in each city
major_airlines_in_cities = airline_city_counts.groupBy("origin_city", "destination_city").agg(
    max(struct(col("flights_count"), col("airline"))).alias("major_airline_info")
) \
    .select(
    "origin_city",
    "destination_city",
    "major_airline_info.airline",
    "major_airline_info.flights_count"
)

# Count the number of flights per day for the majority airline in each city
total_days = df.select("daysOfWeek").distinct().count()
major_airline_flights_per_day = major_airlines_in_cities.withColumn(
    "Average_flights_per_day", col("flights_count") / total_days
)

# Define the output path
output_path = "/mnt/silverzoneflightdata"

# Save the DataFrame as a Delta table with overwrite option set to true
city_flights.write.format("delta").mode("overwrite").save(output_path + "/Citywise_stats")

# Show the results
print("Major Airlines in Cities with Flight Counts and Flights per Day:")
major_airline_flights_per_day.display()

major_airline_flights_per_day.printSchema()

Major Airlines in Cities with Flight Counts and Flights per Day:


origin_city destination_city airline flights_count Average_flights_per_day Adampur Delhi SpiceJet 6 0.047244094488188976 Adampur Jaipur SpiceJet 3 0.023622047244094488 Adampur Mumbai SpiceJet 4 0.031496062992125984 Agartala Aizwal IndiGo 10 0.07874015748031496 Agartala Bengaluru IndiGo 23 0.18110236220472442 Agartala Chennai IndiGo 2 0.015748031496062992 Agartala Delhi IndiGo 10 0.07874015748031496 Agartala Dibrugarh FlyBig 4 0.031496062992125984 Agartala Guwahati IndiGo 32 0.25196850393700787 Agartala Hyderabad IndiGo 2 0.015748031496062992 Agartala Imphal IndiGo 10 0.07874015748031496 Agartala Kolkata IndiGo 135 1.062992125984252 Agartala Shillong IndiGo 11 0.08661417322834646 Agatti Bengaluru Alliance Air (India) 3 0.023622047244094488 Agatti Kochi Alliance Air (India) 23 0.18110236220472442 Agatti NA Alliance Air (India) 2 0.015748031496062992 Agra Ahmedabad IndiGo 10 0.07874015748031496 Agra Bengaluru IndiGo 13 0.10236220472440945 Agra Bhopal IndiGo 12 0.09448818897637795 Agra Delhi NA 2 0.015748031496062992 Agra Jaipur Alliance Air (India) 8 0.06299212598425197 Agra Khajuraho Air India 3 0.023622047244094488 Agra Lucknow IndiGo 9 0.07086614173228346 Agra Mumbai IndiGo 5 0.03937007874015748 Agra Varanasi IndiGo 1 0.007874015748031496 Ahmedabad Agra IndiGo 8 0.06299212598425197 Ahmedabad Amritsar SpiceJet 10 0.07874015748031496 Ahmedabad Aurangabad TruJet 15 0.11811023622047244 Ahmedabad Bagdogra SpiceJet 17 0.13385826771653545 Ahmedabad Belgaum Star Air 25 0.1968503937007874 Ahmedabad Bengaluru IndiGo 149 1.1732283464566928 Ahmedabad Bhavnagar NA 2 0.015748031496062992 Ahmedabad Bhopal IndiGo 24 0.1889763779527559 Ahmedabad Bhubaneswar IndiGo 31 0.2440944881889764 Ahmedabad Bhuj Star Air 8 0.06299212598425197 Ahmedabad Bikaner Alliance Air (India) 1 0.007874015748031496 Ahmedabad Chandigarh GoAir 52 0.4094488188976378 Ahmedabad Chennai IndiGo 96 0.7559055118110236 Ahmedabad Coimbatore IndiGo 3 0.023622047244094488 Ahmedabad Darbhanga SpiceJet 2 0.015748031496062992 Ahmedabad Dehradun IndiGo 20 0.15748031496062992 Ahmedabad Delhi IndiGo 266 2.094488188976378 Ahmedabad Diu NA 2 0.015748031496062992 Ahmedabad Goa IndiGo 55 0.4330708661417323 Ahmedabad Gorakhpur SpiceJet 1 0.007874015748031496 Ahmedabad Guwahati IndiGo 8 0.06299212598425197 Ahmedabad Gwalior SpiceJet 7 0.05511811023622047 Ahmedabad Hubli IndiGo 11 0.08661417322834646 Ahmedabad Hyderabad IndiGo 74 0.5826771653543307 Ahmedabad Indore IndiGo 37 0.29133858267716534 Ahmedabad Jabalpur SpiceJet 5 0.03937007874015748 Ahmedabad Jaipur IndiGo 87 0.6850393700787402 Ahmedabad Jaisalmer TruJet 12 0.09448818897637795 Ahmedabad Jalgaon TruJet 23 0.18110236220472442 Ahmedabad Jammu GoAir 12 0.09448818897637795 Ahmedabad Jamnagar NA 1 0.007874015748031496 Ahmedabad Jodhpur IndiGo 9 0.07086614173228346 Ahmedabad Kandla TruJet 14 0.11023622047244094 Ahmedabad Kannur International Airport GoAir 1 0.007874015748031496 Ahmedabad Kanpur SpiceJet 4 0.031496062992125984 Ahmedabad Keshod TruJet 6 0.047244094488188976 Ahmedabad Kishangarh Star Air 9 0.07086614173228346 Ahmedabad Kochi IndiGo 28 0.2204724409448819 Ahmedabad Kolhapur IndiGo 14 0.11023622047244094 Ahmedabad Kolkata IndiGo 104 0.8188976377952756 Ahmedabad Leh IndiGo 3 0.023622047244094488 Ahmedabad Lucknow IndiGo 59 0.4645669291338583 Ahmedabad MIHAN IndiGo 44 0.3464566929133858 Ahmedabad Mangalore GoAir 6 0.047244094488188976 Ahmedabad Mumbai GoAir 134 1.0551181102362204 Ahmedabad Mundra NA 2 0.015748031496062992 Ahmedabad NA TruJet 19 0.14960629921259844 Ahmedabad Nagpur IndiGo 44 0.3464566929133858 Ahmedabad Nasik Alliance Air (India) 37 0.29133858267716534 Ahmedabad Patna IndiGo 26 0.2047244094488189 Ahmedabad Porbandar TruJet 6 0.047244094488188976 Ahmedabad Pune IndiGo 86 0.6771653543307087 Ahmedabad Raipur IndiGo 15 0.11811023622047244 Ahmedabad Ranchi IndiGo 15 0.11811023622047244 Ahmedabad Shirdi Airport SpiceJet 3 0.023622047244094488 Ahmedabad Srinagar IndiGo 8 0.06299212598425197 Ahmedabad Udaipur SpiceJet 6 0

root
 |-- origin_city: string (nullable = false)
 |-- destination_city: string (nullable = false)
 |-- airline: string (nullable = true)
 |-- flights_count: long (nullable = true)
 |-- Average_flights_per_day: double (nullable = true)



#Oldest Record in the dataset and Newest

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import min, max, to_date, col

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Dataset Date Range") \
    .getOrCreate()

# Read the Parquet file into a DataFrame
parquet_file_path = "/mnt/bronzezoneconversions/Flight_Schedule.parquet"
df = spark.read.parquet(parquet_file_path)

# Define the relevant date columns
date_columns = ["validFrom", "validTo", "lastUpdated"]

# Convert date columns to date type if they are not already in date format
for column in date_columns:
    df = df.withColumn(column, to_date(col(column), "dd-MM-yyyy"))

# Find the oldest and newest dates in the dataset
oldest_date = df.select(min(col("validFrom"))).first()[0]
newest_date = df.select(max(col("validTo"))).first()[0]

# Show the result
print("Oldest date in the dataset:", oldest_date)
print("Newest date in the dataset:", newest_date)


Oldest date in the dataset: 2018-10-28
Newest date in the dataset: 2023-10-28


In [0]:
# Read delta tables into DataFrames
flight_data_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/Flight Data")
city_flights_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/city_flights")
city_wise_stats_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/Citywise_stats")

# Create fact table (flight_data)
flight_data_df.createOrReplaceTempView("flight_data")
fact_table = spark.sql("""
    SELECT airline,
           total_flights_count,
           avg_flights_per_day_count,
           market_share_percentage,
           top_airlines_total_flights
    FROM flight_data
""")
fact_table.write.format("delta").save("/mnt/goldzoneflightstats/fact_flight_data")

# Create dimension table (city_flights)
city_flights_df.createOrReplaceTempView("city_flights")
dimension_table_city_flights = spark.sql("""
    SELECT city,
           inbound_flights,
           outbound_flights,
           total_flights
    FROM city_flights
""")
dimension_table_city_flights.write.format("delta").save("/mnt/goldzoneflightstats/dim_city_flights")




---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-4382248656589254>, line 16
      7 flight_data_df.createOrReplaceTempView("flight_data")
      8 fact_table = spark.sql("""
      9     SELECT airline,
     10            total_flights_count,
   (...)
     14     FROM flight_data
     15 """)
---> 16 fact_table.write.format("delta").save("/mnt/goldzoneflightstats/fact_flight_data")
     18 # Create dimension table (city_flights)
     19 city_flights_df.createOrReplaceTempView("city_flights")

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databric

In [0]:
# Check the schema of city_wise_stats_df
city_wise_stats_df.printSchema()


In [0]:
# Read delta tables into DataFrames
flight_data_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/Flight Data")
city_flights_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/city_flights")
city_wise_stats_df = spark.read.format("delta").load("/mnt/silverzoneflightdata/Citywise_stats")

# Create fact table (flight_data)
flight_data_df.createOrReplaceTempView("flight_data")
fact_table = spark.sql("""
    SELECT airline,
           total_flights_count,
           avg_flights_per_day_count,
           market_share_percentage,
           top_airlines_total_flights
    FROM flight_data
""")
fact_table.write.format("delta").save("/mnt/goldzoneflightstats/fact_flight_data")

# Create dimension table (city_flights)
city_flights_df.createOrReplaceTempView("city_flights")
dimension_table_city_flights = spark.sql("""
    SELECT city,
           inbound_flights,
           outbound_flights,
           total_flights
    FROM city_flights
""")
dimension_table_city_flights.write.format("delta").save("/mnt/goldzoneflightstats/dim_city_flights")




---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-2390626644991647>, line 16
      7 flight_data_df.createOrReplaceTempView("flight_data")
      8 fact_table = spark.sql("""
      9     SELECT airline,
     10            total_flights_count,
   (...)
     14     FROM flight_data
     15 """)
---> 16 fact_table.write.format("delta").save("/mnt/goldzoneflightstats/fact_flight_data")
     18 # Create dimension table (city_flights)
     19 city_flights_df.createOrReplaceTempView("city_flights")

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databric